In [1]:
from bs4 import BeautifulSoup as bs
import requests
import random
import time
import re
import pandas as pd

In [2]:
def get_price(product):
    # includes regex expressions to extract the price as avalue away from the '$' and ","
    product_price = 'N/A'
    try:
        product_price = product.find('p', {'class', 'price'}).text
    except AttributeError:
        print('missing price')
    if product_price.find('$') != -1:
        p = product_price.split("$")
        car_price = p[1]
        price = int(car_price.replace(',' , ''))
        return price
    else:
        return product_price

In [3]:
def get_title(product):
    #includes regex expression to extract brand,year, and model seperately
    list_brands = ["Alfa Romeo", "Asia", "Aston Martin", "Audi", "Bentley", "BMW", "Buick", "Cadillac", "Chery", "Chevrolet", "Chrysler",  "Citroen", "Daihatsu", "Dodge", "Ferrari", "Fiat", "Ford", "Foton", "Geely", "GMC", "Great Wall", "Haval", "Hino", "Holden", "Honda", "HSV", "Hummer", "Hyundai", "Infiniti", "Isuzu", "Jaguar", "Jeep", "Kia", "Lamborghini", "LDV", "Lexus", "Lincoln", "Mahindra", "Maserati", "Mazda", "Mclaren", "Mercedes-Benz", "MG", "Mini", "Mitsubishi", "Nissan", "Oldsmobile", "Opel", "Peugeot", "Pontiac", "Porsche", "Ram",  "Renault", "Rolls-Royce", "Rover", "Saab", "Skoda", "Smart", "Ssangyong", "Subaru", "Suzuki", "Tesla", "Toyota", "Triumph", "Vauxhall", "Volkswagen", "Volvo", "Chrysler Jeep", "Range Rover", "Land Rover"]
    product_title = 'N/A'
    try:
        product_title = product.find('p', {'class', 'title'}).text
    except AttributeError:
        print('missing title')
    t = product_title.split(" ", 2)
    caryear = t[0]
    for brand in list_brands:
        if product_title.find(brand) != -1:
            carbrand = brand
            m = product_title.split(carbrand)
            carmodel = m[-1]
            #break
    features_dict = {
        "year": caryear,
        "brand": carbrand,
        "model": carmodel
    }                
    return features_dict

In [4]:
def get_seller_info(product):
    # gets seller type and location
    product_info = 'N/A'
    try:
        product_info = product.find('p', {'class', 'dealer'}).text
    except AttributeError:
        print('missing info')
    info = product_info.split(",")
    return info

In [5]:
def get_features(product):
    # returns a string containing features about the car
    product_features = 'N/A'
    try:
        product_features = product.find('ul', {'class', 'features'}).text
    except AttributeError:
        print('missing feature')
    return product_features

In [6]:
def split_feature(features):
    #splits the sting returned from get_features by using several regex expressions to extract details about the car
    #list of features extracted from https://www.autotrader.co.nz/advanced-search
    feature = features.split("\n")
    listBodytype = ["4X4", "4x4", "Convertible", "Coupe", "Hatchback", "People Mover", "Sedan", "Small Truck", "SUV", "Suv", "Ute", "Van And Minivan", "Wagon"]
    listTransmission = ["Automatic", "Continuous Variable", "Manual", "Tiptronic"]
    listcolour = ["Beige", "Black", "Blue", "Bronze", "Brown", "Gold", "Green", "Grey", "Maroon","Orange","Pink", "Purple", "Red", "Silver", "White", "Yellow"]
    listfueltype = ["Diesel", "Dual Fuel", "Electric", "Hybrid", "Lpg", "Petrol", "Unleaded"]
    
    mileage = 'N/A'
    doors = 'N/A'
    engine = 'N/A'
    carfuel = 'N/A'
    cartype = 'N/A'
    cartransmission = 'N/A'
    carcolour = 'N/A'
    for i in range (len(feature)):
        f = feature[i]
        if f.find('km') != -1:
            p = f.split("km")
            mileage_comma= p[0]
            if any(char.isdigit() for char in mileage_comma):
                miles = mileage_comma.replace(',', '')
                mileage = int(miles)
            else:
                mileage = 'N/A'
        if f.find('Door') != -1:
            cardoors = f.split("Door")
            cardoor = cardoors[0].split(" ")
            doors = cardoor[-2]
        if f.find('cc') != -1:
            sizes = f.split("cc")
            size = sizes[0].split(" ")
            engine = size[-1]
        for bodytype in listBodytype:
            if f.find(bodytype) != -1:
                cartype = bodytype
                cartype = cartype.title();
        for transmission in listTransmission:
            if f.find(transmission) != -1:
                cartransmission = transmission
        for colour in listcolour:
            if f.find(colour) != -1:
                carcolour = colour
        for fueltype in listfueltype:
            if f.find(fueltype) != -1:
                carfuel = fueltype
  
    features_dict = {
        "mileage": mileage,
        "doors": doors,
        "engine": engine,
        "carfuel": carfuel,
        "cartype": cartype,
        "cartransmission": cartransmission,
        "carcolour": carcolour,
    }
    return features_dict

In [7]:
def get_link(product):
    # gets url link to each car for debugging
    product_link = 'N/A'
    try:
        product_info = product.find('p', {'class', 'title'})
        link = str(product_info.find("a")).split("\"")[1]
        product_link = "https://www.autotrader.co.nz" + str(link)
    except AttributeError:
        print('missing link')
    return product_link

In [8]:
def scrap(url, sort_by, header):
    #extracts information from link
    product_dict = {}
    
    index = 1
    for page in range(1,751):
        wait_time = random.uniform(7,16)
        time.sleep(wait_time)
        print ("Scraping: " + url + '?page=' + str(page) + sort_by)
        response = requests.get(url +  '?page=' + str(page) + sort_by, headers=header)
        html = response.content
        page_soup = bs(html, 'lxml')
        products = page_soup.find_all('div', {'class' : ['list-item ', 'list-item premium-listing']})
            
        if products is None:
            print('No products found')
            break
               
        rank_count = 1
        for product in products:            
            title = get_title(product)              
            features = get_features(product)
            a = split_feature(features)                       
            b = get_seller_info(product)
            sellertype = b[0]
            sellerlocation = b[1].lstrip().title()
            if sellerlocation == "":
                sellerlocation = 'N/A'
            link = get_link(product)
            product_dict[index] = {
                    "year" : title["year"],
                    "brand" : title["brand"],
                    "model" : title["model"],
                    "price ($)" : get_price(product),
                    "mileage (km)" : a["mileage"],
                    "door_number": a["doors"],
                    "engine_size (cc)": a["engine"],
                    "fuel_type": a["carfuel"],
                    "bodystyle": a["cartype"],
                    "transmission": a["cartransmission"],
                    "colour": a["carcolour"],
                    "seller_type": sellertype,
                    "seller_location": sellerlocation,
                    "page" : page,
                    "page_rank" : rank_count,
                    "link" : link
                    }
            rank_count = rank_count + 1
            index = index + 1
            #print("-------------------------------------------------------------------------------------")
        print("Number of products scrapped: " + str(len(product_dict)))
        #break # limit one page      
    return product_dict         

In [9]:
#code adapted from training day demo
base_url = "http://www.autotrader.co.nz/used-cars-for-sale"
sort_by = "&sort=MostPopular"

# do get request using request library
header={'user-agent':''}

response = requests.get(base_url, headers=header) # requires user aganet header

#check if response was successful - expect 200 back if successful
#print(response.status_code)

#check content
#print(response.content)

#stop if not 200
if response.status_code != 200:
    print("Error: " + response.status_code)
    exit(0)
else:
    print("Response: " + str(response.status_code))
    
    #print html to see if getting anything back
print(response)


products = scrap(base_url, sort_by, header)

print("Total number of products scraped: " + str(len(products)))
for keys,values in products.items():
    print(keys)
    print(values)

Response: 200
<Response [200]>
Scraping: http://www.autotrader.co.nz/used-cars-for-sale?page=1&sort=MostPopular
Number of products scrapped: 20
Scraping: http://www.autotrader.co.nz/used-cars-for-sale?page=2&sort=MostPopular
Number of products scrapped: 40
Scraping: http://www.autotrader.co.nz/used-cars-for-sale?page=3&sort=MostPopular
Number of products scrapped: 60
Scraping: http://www.autotrader.co.nz/used-cars-for-sale?page=4&sort=MostPopular
Number of products scrapped: 80
Scraping: http://www.autotrader.co.nz/used-cars-for-sale?page=5&sort=MostPopular
Number of products scrapped: 100
Scraping: http://www.autotrader.co.nz/used-cars-for-sale?page=6&sort=MostPopular
Number of products scrapped: 120
Scraping: http://www.autotrader.co.nz/used-cars-for-sale?page=7&sort=MostPopular
Number of products scrapped: 140
Scraping: http://www.autotrader.co.nz/used-cars-for-sale?page=8&sort=MostPopular
Number of products scrapped: 160
Scraping: http://www.autotrader.co.nz/used-cars-for-sale?page

Scraping: http://www.autotrader.co.nz/used-cars-for-sale?page=72&sort=MostPopular
Number of products scrapped: 1440
Scraping: http://www.autotrader.co.nz/used-cars-for-sale?page=73&sort=MostPopular
Number of products scrapped: 1460
Scraping: http://www.autotrader.co.nz/used-cars-for-sale?page=74&sort=MostPopular
Number of products scrapped: 1480
Scraping: http://www.autotrader.co.nz/used-cars-for-sale?page=75&sort=MostPopular
Number of products scrapped: 1500
Scraping: http://www.autotrader.co.nz/used-cars-for-sale?page=76&sort=MostPopular
Number of products scrapped: 1520
Scraping: http://www.autotrader.co.nz/used-cars-for-sale?page=77&sort=MostPopular
Number of products scrapped: 1540
Scraping: http://www.autotrader.co.nz/used-cars-for-sale?page=78&sort=MostPopular
Number of products scrapped: 1560
Scraping: http://www.autotrader.co.nz/used-cars-for-sale?page=79&sort=MostPopular
Number of products scrapped: 1580
Scraping: http://www.autotrader.co.nz/used-cars-for-sale?page=80&sort=Mo

Number of products scrapped: 2840
Scraping: http://www.autotrader.co.nz/used-cars-for-sale?page=143&sort=MostPopular
Number of products scrapped: 2860
Scraping: http://www.autotrader.co.nz/used-cars-for-sale?page=144&sort=MostPopular
Number of products scrapped: 2880
Scraping: http://www.autotrader.co.nz/used-cars-for-sale?page=145&sort=MostPopular
Number of products scrapped: 2900
Scraping: http://www.autotrader.co.nz/used-cars-for-sale?page=146&sort=MostPopular
Number of products scrapped: 2920
Scraping: http://www.autotrader.co.nz/used-cars-for-sale?page=147&sort=MostPopular
Number of products scrapped: 2940
Scraping: http://www.autotrader.co.nz/used-cars-for-sale?page=148&sort=MostPopular
Number of products scrapped: 2960
Scraping: http://www.autotrader.co.nz/used-cars-for-sale?page=149&sort=MostPopular
Number of products scrapped: 2980
Scraping: http://www.autotrader.co.nz/used-cars-for-sale?page=150&sort=MostPopular
Number of products scrapped: 3000
Scraping: http://www.autotrade

Scraping: http://www.autotrader.co.nz/used-cars-for-sale?page=213&sort=MostPopular
Number of products scrapped: 4260
Scraping: http://www.autotrader.co.nz/used-cars-for-sale?page=214&sort=MostPopular
Number of products scrapped: 4280
Scraping: http://www.autotrader.co.nz/used-cars-for-sale?page=215&sort=MostPopular
Number of products scrapped: 4300
Scraping: http://www.autotrader.co.nz/used-cars-for-sale?page=216&sort=MostPopular
Number of products scrapped: 4320
Scraping: http://www.autotrader.co.nz/used-cars-for-sale?page=217&sort=MostPopular
Number of products scrapped: 4340
Scraping: http://www.autotrader.co.nz/used-cars-for-sale?page=218&sort=MostPopular
Number of products scrapped: 4360
Scraping: http://www.autotrader.co.nz/used-cars-for-sale?page=219&sort=MostPopular
Number of products scrapped: 4380
Scraping: http://www.autotrader.co.nz/used-cars-for-sale?page=220&sort=MostPopular
Number of products scrapped: 4400
Scraping: http://www.autotrader.co.nz/used-cars-for-sale?page=22

Number of products scrapped: 5660
Scraping: http://www.autotrader.co.nz/used-cars-for-sale?page=284&sort=MostPopular
Number of products scrapped: 5680
Scraping: http://www.autotrader.co.nz/used-cars-for-sale?page=285&sort=MostPopular
Number of products scrapped: 5700
Scraping: http://www.autotrader.co.nz/used-cars-for-sale?page=286&sort=MostPopular
Number of products scrapped: 5720
Scraping: http://www.autotrader.co.nz/used-cars-for-sale?page=287&sort=MostPopular
Number of products scrapped: 5740
Scraping: http://www.autotrader.co.nz/used-cars-for-sale?page=288&sort=MostPopular
Number of products scrapped: 5760
Scraping: http://www.autotrader.co.nz/used-cars-for-sale?page=289&sort=MostPopular
Number of products scrapped: 5780
Scraping: http://www.autotrader.co.nz/used-cars-for-sale?page=290&sort=MostPopular
Number of products scrapped: 5800
Scraping: http://www.autotrader.co.nz/used-cars-for-sale?page=291&sort=MostPopular
Number of products scrapped: 5820
Scraping: http://www.autotrade

...

14413
{'year': '2017', 'brand': 'Toyota', 'model': ' Rav4', 'price ($)': 28888, 'mileage (km)': 46900, 'door_number': 'N/A', 'engine_size (cc)': '2494', 'fuel_type': 'Petrol', 'bodystyle': 'Wagon', 'transmission': 'Automatic', 'colour': 'N/A', 'seller_type': 'Dealer', 'seller_location': 'Auckland', 'page': 724, 'page_rank': 13, 'link': 'https://www.autotrader.co.nz/used-cars-for-sale/toyota-rav4/2092168'}
14414
{'year': '2010', 'brand': 'Mazda', 'model': ' Axela', 'price ($)': 10990, 'mileage (km)': 81568, 'door_number': 'N/A', 'engine_size (cc)': '1500', 'fuel_type': 'Petrol', 'bodystyle': 'Hatchback', 'transmission': 'Automatic', 'colour': 'Red', 'seller_type': 'Dealer', 'seller_location': 'Auckland', 'page': 724, 'page_rank': 14, 'link': 'https://www.autotrader.co.nz/used-cars-for-sale/mazda-axela/2091836'}
14415
{'year': '2011', 'brand': 'Mitsubishi', 'model': ' Triton', 'price ($)': 22995, 'mileage (km)': 218261, 'door_number': 'N/A', 'engine_size (cc)': '2500', 'fuel_type': 'Dies

14578
{'year': '2013', 'brand': 'Mitsubishi', 'model': ' Outlander', 'price ($)': 11990, 'mileage (km)': 196000, 'door_number': '5', 'engine_size (cc)': '2000', 'fuel_type': 'Petrol', 'bodystyle': 'Suv', 'transmission': 'Automatic', 'colour': 'Black', 'seller_type': 'Dealer', 'seller_location': 'Manawatu Wanganui', 'page': 732, 'page_rank': 18, 'link': 'https://www.autotrader.co.nz/used-cars-for-sale/mitsubishi-outlander/2102561'}
14579
{'year': '2017', 'brand': 'Suzuki', 'model': ' Swift', 'price ($)': 17999, 'mileage (km)': 1687, 'door_number': 'N/A', 'engine_size (cc)': '1200', 'fuel_type': 'Petrol', 'bodystyle': 'Hatchback', 'transmission': 'Automatic', 'colour': 'Silver', 'seller_type': 'Dealer', 'seller_location': 'Nelson', 'page': 732, 'page_rank': 19, 'link': 'https://www.autotrader.co.nz/used-cars-for-sale/suzuki-swift/2102520'}
14580
{'year': '2006', 'brand': 'Mitsubishi', 'model': ' Challenger', 'price ($)': 24995, 'mileage (km)': 28600, 'door_number': 'N/A', 'engine_size (c

{'year': '2006', 'brand': 'Nissan', 'model': ' March', 'price ($)': 4990, 'mileage (km)': 83903, 'door_number': 'N/A', 'engine_size (cc)': '1200', 'fuel_type': 'Petrol', 'bodystyle': 'N/A', 'transmission': 'Automatic', 'colour': 'Silver', 'seller_type': 'Dealer', 'seller_location': 'Canterbury', 'page': 738, 'page_rank': 13, 'link': 'https://www.autotrader.co.nz/used-cars-for-sale/nissan-march/2099483'}
14694
{'year': '2006', 'brand': 'Honda', 'model': ' Odyssey', 'price ($)': 5480, 'mileage (km)': 121100, 'door_number': 'N/A', 'engine_size (cc)': '2400', 'fuel_type': 'Petrol', 'bodystyle': 'Wagon', 'transmission': 'Automatic', 'colour': 'N/A', 'seller_type': 'Dealer', 'seller_location': 'Auckland', 'page': 738, 'page_rank': 14, 'link': 'https://www.autotrader.co.nz/used-cars-for-sale/honda-odyssey/2099480'}
14695
{'year': '2016', 'brand': 'Holden', 'model': ' Captiva', 'price ($)': 26800, 'mileage (km)': 49450, 'door_number': 'N/A', 'engine_size (cc)': '3000', 'fuel_type': 'Petrol', '

14775
{'year': '2019', 'brand': 'Suzuki', 'model': ' Swift', 'price ($)': 23990, 'mileage (km)': 100, 'door_number': 'N/A', 'engine_size (cc)': '1242', 'fuel_type': 'Petrol', 'bodystyle': 'Hatchback', 'transmission': 'Automatic', 'colour': 'Blue', 'seller_type': 'Dealer', 'seller_location': 'Auckland', 'page': 742, 'page_rank': 15, 'link': 'https://www.autotrader.co.nz/used-cars-for-sale/suzuki-swift/2108532'}
14776
{'year': '2015', 'brand': 'Nissan', 'model': ' Pulsar', 'price ($)': 11990, 'mileage (km)': 90000, 'door_number': 'N/A', 'engine_size (cc)': '1798', 'fuel_type': 'Petrol', 'bodystyle': 'Sedan', 'transmission': 'Automatic', 'colour': 'White', 'seller_type': 'Dealer', 'seller_location': 'Canterbury', 'page': 742, 'page_rank': 16, 'link': 'https://www.autotrader.co.nz/used-cars-for-sale/nissan-pulsar/2108520'}
14777
{'year': '2007', 'brand': 'Nissan', 'model': ' Bluebird', 'price ($)': 5795, 'mileage (km)': 49898, 'door_number': 'N/A', 'engine_size (cc)': '2000', 'fuel_type': 

14939
{'year': '2009', 'brand': 'Toyota', 'model': ' Corolla', 'price ($)': 8990, 'mileage (km)': 159383, 'door_number': 'N/A', 'engine_size (cc)': '1800', 'fuel_type': 'Petrol', 'bodystyle': 'Hatchback', 'transmission': 'Automatic', 'colour': 'Red', 'seller_type': 'Dealer', 'seller_location': 'Southland', 'page': 750, 'page_rank': 19, 'link': 'https://www.autotrader.co.nz/used-cars-for-sale/toyota-corolla/2096584'}
14940
{'year': '2010', 'brand': 'Nissan', 'model': ' Skyline', 'price ($)': 9995, 'mileage (km)': 118264, 'door_number': '4', 'engine_size (cc)': '2500', 'fuel_type': 'Petrol', 'bodystyle': 'Sedan', 'transmission': 'Automatic', 'colour': 'Silver', 'seller_type': 'Dealer', 'seller_location': 'Manawatu Wanganui', 'page': 750, 'page_rank': 20, 'link': 'https://www.autotrader.co.nz/used-cars-for-sale/nissan-skyline/2096220'}


In [10]:
# write results to a file
df = pd.DataFrame.from_dict(products, orient='index')
df.to_csv('./output-test-15000.csv')